In [1]:
from common import *

In [2]:
fnames = glob('../data/lingvo/raw/*')

In [3]:
dim = 300

In [4]:
import gc, io

prog = re.compile("[\W\d]", re.UNICODE)

def process(fnames, i):
    with io.open('../data/lingvo/%s.txt'%i, 'w', encoding='utf8') as fw:
        for fn in fnames:
            with io.open(fn, encoding='utf8') as fr:
                text = fr.read()
            sents = sent_tokenize(text)
            sents = [[w for w in s.split() if w not in stop_list and len(w)>1] 
                     for s in sents]
            sents = [s for s in sents if len(s)]
            s = json.dumps((basename(fn).split('.')[0], sents))            
            fw.write(s + u'\n')
    gc.collect()


In [10]:
parallelizer = Parallel(n_jobs=cpu_count-1)

tasks_iterator = ( delayed(process)(list_block, i) for 
                  i, list_block in enumerate(grouper(len(fnames)//500, fnames)) ) 
result = parallelizer( tasks_iterator )

In [ ]:
pwd = !pwd
%cd ../data/lingvo/
!cat *.txt > corpus_json.txt&&gzip -f corpus_json.txt&&rm *.txt
%cd {pwd[0]}

^C
/notebooks/pat


In [5]:
import ujson

def iter_docs():
    with GzipFile('../data/lingvo/corpus_json.txt.gz', 'r') as fr:
        for line in fr:
            _id, sents = ujson.loads(line)
            yield _id, sents
    
def iter_sents():
    for _id, sents in iter_docs():
        for s in sents:
            yield s
                
class Sentences(object):
    def __iter__(self):
        for sent in iter_sents():
            yield sent
            
class Documents(object):
    def __iter__(self):
        for _id, doc in iter_docs():
            unlisted = [w for s in doc for w in s]
            yield gensim.models.doc2vec.TaggedDocument(unlisted, [_id])

In [13]:
bigram = gensim.models.Phrases(iter_sents())

2017-10-23 14:15:51,409 [MainThread  ] [INFO ]  collecting all words and their counts
2017-10-23 14:15:51,413 [MainThread  ] [INFO ]  PROGRESS: at sentence #0, processed 0 words and 0 word types
2017-10-23 14:15:51,685 [MainThread  ] [INFO ]  PROGRESS: at sentence #10000, processed 123763 words and 68811 word types
2017-10-23 14:15:51,924 [MainThread  ] [INFO ]  PROGRESS: at sentence #20000, processed 247232 words and 126750 word types
2017-10-23 14:15:52,157 [MainThread  ] [INFO ]  PROGRESS: at sentence #30000, processed 361814 words and 181905 word types
2017-10-23 14:15:52,417 [MainThread  ] [INFO ]  PROGRESS: at sentence #40000, processed 476326 words and 236790 word types
2017-10-23 14:15:52,631 [MainThread  ] [INFO ]  PROGRESS: at sentence #50000, processed 582163 words and 284932 word types
2017-10-23 14:15:52,877 [MainThread  ] [INFO ]  PROGRESS: at sentence #60000, processed 707456 words and 338864 word types
2017-10-23 14:15:53,148 [MainThread  ] [INFO ]  PROGRESS: at sentenc

2017-10-23 14:16:07,146 [MainThread  ] [INFO ]  PROGRESS: at sentence #650000, processed 7567876 words and 2647655 word types
2017-10-23 14:16:07,375 [MainThread  ] [INFO ]  PROGRESS: at sentence #660000, processed 7682367 words and 2681041 word types
2017-10-23 14:16:07,620 [MainThread  ] [INFO ]  PROGRESS: at sentence #670000, processed 7807102 words and 2711419 word types
2017-10-23 14:16:07,872 [MainThread  ] [INFO ]  PROGRESS: at sentence #680000, processed 7928153 words and 2745114 word types
2017-10-23 14:16:08,134 [MainThread  ] [INFO ]  PROGRESS: at sentence #690000, processed 8055747 words and 2778601 word types
2017-10-23 14:16:08,493 [MainThread  ] [INFO ]  PROGRESS: at sentence #700000, processed 8174804 words and 2811945 word types
2017-10-23 14:16:08,720 [MainThread  ] [INFO ]  PROGRESS: at sentence #710000, processed 8289637 words and 2843494 word types
2017-10-23 14:16:08,960 [MainThread  ] [INFO ]  PROGRESS: at sentence #720000, processed 8407980 words and 2876660 wor

2017-10-23 14:16:22,820 [MainThread  ] [INFO ]  PROGRESS: at sentence #1300000, processed 15124310 words and 4663688 word types
2017-10-23 14:16:23,073 [MainThread  ] [INFO ]  PROGRESS: at sentence #1310000, processed 15239642 words and 4693827 word types
2017-10-23 14:16:23,314 [MainThread  ] [INFO ]  PROGRESS: at sentence #1320000, processed 15354120 words and 4723914 word types
2017-10-23 14:16:23,563 [MainThread  ] [INFO ]  PROGRESS: at sentence #1330000, processed 15475762 words and 4753731 word types
2017-10-23 14:16:23,792 [MainThread  ] [INFO ]  PROGRESS: at sentence #1340000, processed 15589302 words and 4782687 word types
2017-10-23 14:16:24,023 [MainThread  ] [INFO ]  PROGRESS: at sentence #1350000, processed 15699310 words and 4810258 word types
2017-10-23 14:16:24,266 [MainThread  ] [INFO ]  PROGRESS: at sentence #1360000, processed 15816553 words and 4845228 word types
2017-10-23 14:16:24,517 [MainThread  ] [INFO ]  PROGRESS: at sentence #1370000, processed 15935536 words

2017-10-23 14:16:38,513 [MainThread  ] [INFO ]  PROGRESS: at sentence #1950000, processed 22633648 words and 6459857 word types
2017-10-23 14:16:38,743 [MainThread  ] [INFO ]  PROGRESS: at sentence #1960000, processed 22746937 words and 6487341 word types
2017-10-23 14:16:38,985 [MainThread  ] [INFO ]  PROGRESS: at sentence #1970000, processed 22866400 words and 6514215 word types
2017-10-23 14:16:39,223 [MainThread  ] [INFO ]  PROGRESS: at sentence #1980000, processed 22986199 words and 6542427 word types
2017-10-23 14:16:39,463 [MainThread  ] [INFO ]  PROGRESS: at sentence #1990000, processed 23102422 words and 6566742 word types
2017-10-23 14:16:39,702 [MainThread  ] [INFO ]  PROGRESS: at sentence #2000000, processed 23221602 words and 6590987 word types
2017-10-23 14:16:39,933 [MainThread  ] [INFO ]  PROGRESS: at sentence #2010000, processed 23334692 words and 6618638 word types
2017-10-23 14:16:40,170 [MainThread  ] [INFO ]  PROGRESS: at sentence #2020000, processed 23448025 words

2017-10-23 14:16:53,847 [MainThread  ] [INFO ]  PROGRESS: at sentence #2600000, processed 30171468 words and 8115170 word types
2017-10-23 14:16:54,081 [MainThread  ] [INFO ]  PROGRESS: at sentence #2610000, processed 30282077 words and 8141265 word types
2017-10-23 14:16:54,329 [MainThread  ] [INFO ]  PROGRESS: at sentence #2620000, processed 30407113 words and 8165944 word types
2017-10-23 14:16:54,576 [MainThread  ] [INFO ]  PROGRESS: at sentence #2630000, processed 30526852 words and 8189657 word types
2017-10-23 14:16:54,825 [MainThread  ] [INFO ]  PROGRESS: at sentence #2640000, processed 30648527 words and 8211262 word types
2017-10-23 14:16:55,065 [MainThread  ] [INFO ]  PROGRESS: at sentence #2650000, processed 30765897 words and 8235159 word types
2017-10-23 14:16:55,294 [MainThread  ] [INFO ]  PROGRESS: at sentence #2660000, processed 30878939 words and 8258875 word types
2017-10-23 14:16:55,527 [MainThread  ] [INFO ]  PROGRESS: at sentence #2670000, processed 30993622 words

...

2017-10-23 14:56:47,152 [MainThread  ] [INFO ]  PROGRESS: at sentence #90870000, processed 1058545050 words and 36862350 word types
2017-10-23 14:56:47,386 [MainThread  ] [INFO ]  PROGRESS: at sentence #90880000, processed 1058658537 words and 36874084 word types
2017-10-23 14:56:47,632 [MainThread  ] [INFO ]  PROGRESS: at sentence #90890000, processed 1058775527 words and 36888655 word types
2017-10-23 14:56:47,881 [MainThread  ] [INFO ]  PROGRESS: at sentence #90900000, processed 1058895184 words and 36901436 word types
2017-10-23 14:56:48,131 [MainThread  ] [INFO ]  PROGRESS: at sentence #90910000, processed 1059012831 words and 36914165 word types
2017-10-23 14:56:48,380 [MainThread  ] [INFO ]  PROGRESS: at sentence #90920000, processed 1059132328 words and 36925697 word types
2017-10-23 14:56:48,633 [MainThread  ] [INFO ]  PROGRESS: at sentence #90930000, processed 1059254996 words and 36937568 word types
2017-10-23 14:56:48,867 [MainThread  ] [INFO ]  PROGRESS: at sentence #90940

2017-10-23 14:57:07,769 [MainThread  ] [INFO ]  PROGRESS: at sentence #91500000, processed 1065909505 words and 37644158 word types
2017-10-23 14:57:07,996 [MainThread  ] [INFO ]  PROGRESS: at sentence #91510000, processed 1066018471 words and 37654835 word types
2017-10-23 14:57:08,234 [MainThread  ] [INFO ]  PROGRESS: at sentence #91520000, processed 1066130600 words and 37667819 word types
2017-10-23 14:57:08,491 [MainThread  ] [INFO ]  PROGRESS: at sentence #91530000, processed 1066252773 words and 37681845 word types
2017-10-23 14:57:08,734 [MainThread  ] [INFO ]  PROGRESS: at sentence #91540000, processed 1066370642 words and 37691721 word types
2017-10-23 14:57:08,976 [MainThread  ] [INFO ]  PROGRESS: at sentence #91550000, processed 1066486380 words and 37703303 word types
2017-10-23 14:57:09,225 [MainThread  ] [INFO ]  PROGRESS: at sentence #91560000, processed 1066605370 words and 37717290 word types
2017-10-23 14:57:09,480 [MainThread  ] [INFO ]  PROGRESS: at sentence #91570

2017-10-23 14:57:23,156 [MainThread  ] [INFO ]  PROGRESS: at sentence #92130000, processed 1073250959 words and 38439765 word types
2017-10-23 14:57:23,383 [MainThread  ] [INFO ]  PROGRESS: at sentence #92140000, processed 1073358454 words and 38454401 word types
2017-10-23 14:57:23,620 [MainThread  ] [INFO ]  PROGRESS: at sentence #92150000, processed 1073471247 words and 38466534 word types
2017-10-23 14:57:23,885 [MainThread  ] [INFO ]  PROGRESS: at sentence #92160000, processed 1073597092 words and 38481513 word types
2017-10-23 14:57:24,135 [MainThread  ] [INFO ]  PROGRESS: at sentence #92170000, processed 1073713659 words and 38495953 word types
2017-10-23 14:57:24,390 [MainThread  ] [INFO ]  PROGRESS: at sentence #92180000, processed 1073835590 words and 38510523 word types
2017-10-23 14:57:24,642 [MainThread  ] [INFO ]  PROGRESS: at sentence #92190000, processed 1073947638 words and 38523705 word types
2017-10-23 14:57:24,906 [MainThread  ] [INFO ]  PROGRESS: at sentence #92200

2017-10-23 14:57:38,847 [MainThread  ] [INFO ]  PROGRESS: at sentence #92760000, processed 1080640918 words and 39225415 word types
2017-10-23 14:57:39,111 [MainThread  ] [INFO ]  PROGRESS: at sentence #92770000, processed 1080769097 words and 39237535 word types
2017-10-23 14:57:39,355 [MainThread  ] [INFO ]  PROGRESS: at sentence #92780000, processed 1080878098 words and 39250326 word types
2017-10-23 14:57:39,613 [MainThread  ] [INFO ]  PROGRESS: at sentence #92790000, processed 1080994216 words and 39264151 word types
2017-10-23 14:57:39,865 [MainThread  ] [INFO ]  PROGRESS: at sentence #92800000, processed 1081109654 words and 39271008 word types
2017-10-23 14:57:40,121 [MainThread  ] [INFO ]  PROGRESS: at sentence #92810000, processed 1081224528 words and 39285659 word types
2017-10-23 14:57:40,372 [MainThread  ] [INFO ]  PROGRESS: at sentence #92820000, processed 1081340810 words and 39296199 word types
2017-10-23 14:57:40,618 [MainThread  ] [INFO ]  PROGRESS: at sentence #92830

2017-10-23 14:57:54,509 [MainThread  ] [INFO ]  PROGRESS: at sentence #93390000, processed 1087979472 words and 39992440 word types
2017-10-23 14:58:21,108 [MainThread  ] [INFO ]  pruned out 26284200 tokens with count <=6 (before 40000001, after 13715801)
2017-10-23 14:58:21,177 [MainThread  ] [INFO ]  PROGRESS: at sentence #93400000, processed 1088096873 words and 13718795 word types
2017-10-23 14:58:21,426 [MainThread  ] [INFO ]  PROGRESS: at sentence #93410000, processed 1088210900 words and 13736213 word types
2017-10-23 14:58:21,685 [MainThread  ] [INFO ]  PROGRESS: at sentence #93420000, processed 1088328342 words and 13756425 word types
2017-10-23 14:58:21,949 [MainThread  ] [INFO ]  PROGRESS: at sentence #93430000, processed 1088454650 words and 13772053 word types
2017-10-23 14:58:22,211 [MainThread  ] [INFO ]  PROGRESS: at sentence #93440000, processed 1088580262 words and 13787336 word types
2017-10-23 14:58:22,470 [MainThread  ] [INFO ]  PROGRESS: at sentence #93450000, pro

In [14]:
bigram.save('../data/lingvo/bigram')

2017-10-23 14:58:34,251 [MainThread  ] [INFO ]  saving Phrases object under ../data/lingvo/bigram, separately None
2017-10-23 14:58:52,822 [MainThread  ] [INFO ]  saved ../data/lingvo/bigram


In [15]:
len(bigram.vocab)

14557616

In [16]:
len(bigram.vocab)

14557616

In [17]:
for phrase, score in bigram.export_phrases(islice(iter_sents(), 1000)):
    print('{0}   {1}'.format(phrase, score))

суперсплав никель   21.3022606177
суперсплав никель   21.3022606177
суперсплав никель   21.3022606177
карбид тантал   13.7427535397
суперсплав никель   21.3022606177
карбид тантал   13.7427535397
молибден вольфрам   23.2113732761
суперсплав никель   21.3022606177
молибден вольфрам   23.2113732761
карбид тантал   13.7427535397
суперсплав никель   21.3022606177
патент сша   11.7227021811
торговый наименование   46.1854482212
mo ta   11.2794752825
кристаллографический ориентация   16.039110751
mo ta   11.2794752825
ti zr   54.402871756
et al   40.2209213278
advance materials   39.3792914258
gas turbine   1476.03880694
advanced materials   234.215248558
cr мо   10.3330782714
hf nb   19.83279486
патент сша   11.7227021811
cr мо   10.3330782714
суперсплав суперсплав   38.3011743359
патент сша   11.7227021811
суперсплав никель   21.3022606177
карбид тантал   13.7427535397
цирконий гафний   40.9307139425
патент сша   11.7227021811
цирконий гафний   40.9307139425
карбид тантал   13.7427535397
д

In [31]:
bigram = gensim.models.phrases.Phrases.load('../data/lingvo/bigram_5_100')

2017-10-09 21:37:51,276 [MainThread  ] [INFO ]  loading Phrases object from ../data/lingvo/bigram_5_100
2017-10-09 21:38:17,725 [MainThread  ] [INFO ]  loaded ../data/lingvo/bigram_5_100


In [18]:
bigram_ph = gensim.models.phrases.Phraser(bigram)

2017-10-23 19:25:31,800 [MainThread  ] [INFO ]  source_vocab length 14557616
2017-10-23 19:25:39,470 [MainThread  ] [INFO ]  Phraser added 50000 phrasegrams
2017-10-23 19:25:46,912 [MainThread  ] [INFO ]  Phraser added 100000 phrasegrams
2017-10-23 19:25:54,396 [MainThread  ] [INFO ]  Phraser added 150000 phrasegrams
2017-10-23 19:26:02,070 [MainThread  ] [INFO ]  Phraser added 200000 phrasegrams
2017-10-23 19:26:09,498 [MainThread  ] [INFO ]  Phraser added 250000 phrasegrams
2017-10-23 19:26:17,145 [MainThread  ] [INFO ]  Phraser added 300000 phrasegrams
2017-10-23 19:26:24,717 [MainThread  ] [INFO ]  Phraser added 350000 phrasegrams
2017-10-23 19:26:32,147 [MainThread  ] [INFO ]  Phraser added 400000 phrasegrams
2017-10-23 19:26:39,652 [MainThread  ] [INFO ]  Phraser added 450000 phrasegrams
2017-10-23 19:26:47,341 [MainThread  ] [INFO ]  Phraser added 500000 phrasegrams
2017-10-23 19:26:54,853 [MainThread  ] [INFO ]  Phraser added 550000 phrasegrams
2017-10-23 19:27:02,590 [MainThre

In [19]:
bigram_ph.save('../data/lingvo/bigram_ph')

2017-10-23 19:28:25,907 [MainThread  ] [INFO ]  saving Phraser object under ../data/lingvo/bigram_ph, separately None
2017-10-23 19:28:27,291 [MainThread  ] [INFO ]  saved ../data/lingvo/bigram_ph


In [39]:
bigram_ph = gensim.models.phrases.Phraser.load('../data/lingvo/bigram_ph')

2017-10-24 12:25:09,652 [MainThread  ] [INFO ]  loading Phraser object from ../data/lingvo/bigram_ph
2017-10-24 12:25:13,416 [MainThread  ] [INFO ]  loaded ../data/lingvo/bigram_ph


In [32]:
trigram = gensim.models.Phrases(bigram_ph[iter_sents()])

2017-10-24 04:33:02,686 [MainThread  ] [INFO ]  collecting all words and their counts
2017-10-24 04:33:02,688 [MainThread  ] [INFO ]  PROGRESS: at sentence #0, processed 0 words and 0 word types
2017-10-24 04:33:03,472 [MainThread  ] [INFO ]  PROGRESS: at sentence #10000, processed 118553 words and 68121 word types
2017-10-24 04:33:04,202 [MainThread  ] [INFO ]  PROGRESS: at sentence #20000, processed 235869 words and 126101 word types
2017-10-24 04:33:04,892 [MainThread  ] [INFO ]  PROGRESS: at sentence #30000, processed 343029 words and 181214 word types
2017-10-24 04:33:05,603 [MainThread  ] [INFO ]  PROGRESS: at sentence #40000, processed 451750 words and 236338 word types
2017-10-24 04:33:06,254 [MainThread  ] [INFO ]  PROGRESS: at sentence #50000, processed 552966 words and 284694 word types
2017-10-24 04:33:06,996 [MainThread  ] [INFO ]  PROGRESS: at sentence #60000, processed 670596 words and 339177 word types
2017-10-24 04:33:07,786 [MainThread  ] [INFO ]  PROGRESS: at sentenc

2017-10-24 04:33:48,960 [MainThread  ] [INFO ]  PROGRESS: at sentence #650000, processed 7164852 words and 2712678 word types
2017-10-24 04:33:49,647 [MainThread  ] [INFO ]  PROGRESS: at sentence #660000, processed 7272406 words and 2747504 word types
2017-10-24 04:33:50,377 [MainThread  ] [INFO ]  PROGRESS: at sentence #670000, processed 7388612 words and 2779107 word types
2017-10-24 04:33:51,219 [MainThread  ] [INFO ]  PROGRESS: at sentence #680000, processed 7504693 words and 2814166 word types
2017-10-24 04:33:51,967 [MainThread  ] [INFO ]  PROGRESS: at sentence #690000, processed 7624699 words and 2849023 word types
2017-10-24 04:33:52,678 [MainThread  ] [INFO ]  PROGRESS: at sentence #700000, processed 7737573 words and 2883726 word types
2017-10-24 04:33:53,378 [MainThread  ] [INFO ]  PROGRESS: at sentence #710000, processed 7847371 words and 2916584 word types
2017-10-24 04:33:54,123 [MainThread  ] [INFO ]  PROGRESS: at sentence #720000, processed 7960162 words and 2951226 wor

2017-10-24 04:34:34,840 [MainThread  ] [INFO ]  PROGRESS: at sentence #1300000, processed 14311466 words and 4824743 word types
2017-10-24 04:34:35,548 [MainThread  ] [INFO ]  PROGRESS: at sentence #1310000, processed 14419712 words and 4856417 word types
2017-10-24 04:34:36,239 [MainThread  ] [INFO ]  PROGRESS: at sentence #1320000, processed 14526127 words and 4888183 word types
2017-10-24 04:34:36,977 [MainThread  ] [INFO ]  PROGRESS: at sentence #1330000, processed 14641867 words and 4919730 word types
2017-10-24 04:34:37,667 [MainThread  ] [INFO ]  PROGRESS: at sentence #1340000, processed 14750230 words and 4950185 word types
2017-10-24 04:34:38,355 [MainThread  ] [INFO ]  PROGRESS: at sentence #1350000, processed 14854922 words and 4979157 word types
2017-10-24 04:34:39,119 [MainThread  ] [INFO ]  PROGRESS: at sentence #1360000, processed 14965748 words and 5015777 word types
2017-10-24 04:34:39,867 [MainThread  ] [INFO ]  PROGRESS: at sentence #1370000, processed 15077258 words

2017-10-24 04:35:22,670 [MainThread  ] [INFO ]  PROGRESS: at sentence #1950000, processed 21416705 words and 6723052 word types
2017-10-24 04:35:23,358 [MainThread  ] [INFO ]  PROGRESS: at sentence #1960000, processed 21523453 words and 6752320 word types
2017-10-24 04:35:24,087 [MainThread  ] [INFO ]  PROGRESS: at sentence #1970000, processed 21637078 words and 6780640 word types
2017-10-24 04:35:24,811 [MainThread  ] [INFO ]  PROGRESS: at sentence #1980000, processed 21749971 words and 6810857 word types
2017-10-24 04:35:25,514 [MainThread  ] [INFO ]  PROGRESS: at sentence #1990000, processed 21860016 words and 6836759 word types
2017-10-24 04:35:26,233 [MainThread  ] [INFO ]  PROGRESS: at sentence #2000000, processed 21973909 words and 6862350 word types
2017-10-24 04:35:26,921 [MainThread  ] [INFO ]  PROGRESS: at sentence #2010000, processed 22081375 words and 6891477 word types
2017-10-24 04:35:27,620 [MainThread  ] [INFO ]  PROGRESS: at sentence #2020000, processed 22188520 words

2017-10-24 04:36:08,800 [MainThread  ] [INFO ]  PROGRESS: at sentence #2600000, processed 28554432 words and 8482037 word types
2017-10-24 04:36:09,488 [MainThread  ] [INFO ]  PROGRESS: at sentence #2610000, processed 28659117 words and 8509858 word types
2017-10-24 04:36:10,239 [MainThread  ] [INFO ]  PROGRESS: at sentence #2620000, processed 28776466 words and 8536132 word types
2017-10-24 04:36:10,964 [MainThread  ] [INFO ]  PROGRESS: at sentence #2630000, processed 28890522 words and 8561415 word types
2017-10-24 04:36:11,691 [MainThread  ] [INFO ]  PROGRESS: at sentence #2640000, processed 29002254 words and 8584485 word types
2017-10-24 04:36:12,409 [MainThread  ] [INFO ]  PROGRESS: at sentence #2650000, processed 29112086 words and 8610442 word types
2017-10-24 04:36:13,110 [MainThread  ] [INFO ]  PROGRESS: at sentence #2660000, processed 29219634 words and 8635771 word types
2017-10-24 04:36:13,811 [MainThread  ] [INFO ]  PROGRESS: at sentence #2670000, processed 29328641 words

...

2017-10-24 06:22:00,944 [MainThread  ] [INFO ]  PROGRESS: at sentence #90850000, processed 1001137146 words and 25110197 word types
2017-10-24 06:22:01,617 [MainThread  ] [INFO ]  PROGRESS: at sentence #90860000, processed 1001244073 words and 25125659 word types
2017-10-24 06:22:02,330 [MainThread  ] [INFO ]  PROGRESS: at sentence #90870000, processed 1001360354 words and 25140036 word types
2017-10-24 06:22:03,002 [MainThread  ] [INFO ]  PROGRESS: at sentence #90880000, processed 1001468723 words and 25154968 word types
2017-10-24 06:22:03,698 [MainThread  ] [INFO ]  PROGRESS: at sentence #90890000, processed 1001580299 words and 25173075 word types
2017-10-24 06:22:04,405 [MainThread  ] [INFO ]  PROGRESS: at sentence #90900000, processed 1001693324 words and 25189640 word types
2017-10-24 06:22:05,103 [MainThread  ] [INFO ]  PROGRESS: at sentence #90910000, processed 1001806339 words and 25205857 word types
2017-10-24 06:22:05,808 [MainThread  ] [INFO ]  PROGRESS: at sentence #90920

2017-10-24 06:22:44,707 [MainThread  ] [INFO ]  PROGRESS: at sentence #91480000, processed 1008117551 words and 26112525 word types
2017-10-24 06:22:45,368 [MainThread  ] [INFO ]  PROGRESS: at sentence #91490000, processed 1008216835 words and 26124982 word types
2017-10-24 06:22:46,068 [MainThread  ] [INFO ]  PROGRESS: at sentence #91500000, processed 1008328770 words and 26142745 word types
2017-10-24 06:22:46,714 [MainThread  ] [INFO ]  PROGRESS: at sentence #91510000, processed 1008431880 words and 26157679 word types
2017-10-24 06:22:47,376 [MainThread  ] [INFO ]  PROGRESS: at sentence #91520000, processed 1008538147 words and 26173823 word types
2017-10-24 06:22:48,105 [MainThread  ] [INFO ]  PROGRESS: at sentence #91530000, processed 1008653804 words and 26191751 word types
2017-10-24 06:22:48,832 [MainThread  ] [INFO ]  PROGRESS: at sentence #91540000, processed 1008766744 words and 26205764 word types
2017-10-24 06:22:49,523 [MainThread  ] [INFO ]  PROGRESS: at sentence #91550

2017-10-24 06:23:28,227 [MainThread  ] [INFO ]  PROGRESS: at sentence #92110000, processed 1015045294 words and 27128613 word types
2017-10-24 06:23:28,940 [MainThread  ] [INFO ]  PROGRESS: at sentence #92120000, processed 1015160720 words and 27143470 word types
2017-10-24 06:23:29,651 [MainThread  ] [INFO ]  PROGRESS: at sentence #92130000, processed 1015274631 words and 27161458 word types
2017-10-24 06:23:30,290 [MainThread  ] [INFO ]  PROGRESS: at sentence #92140000, processed 1015375889 words and 27179265 word types
2017-10-24 06:23:30,961 [MainThread  ] [INFO ]  PROGRESS: at sentence #92150000, processed 1015483207 words and 27194395 word types
2017-10-24 06:23:31,703 [MainThread  ] [INFO ]  PROGRESS: at sentence #92160000, processed 1015603919 words and 27212892 word types
2017-10-24 06:23:32,405 [MainThread  ] [INFO ]  PROGRESS: at sentence #92170000, processed 1015713831 words and 27231278 word types
2017-10-24 06:23:33,117 [MainThread  ] [INFO ]  PROGRESS: at sentence #92180

2017-10-24 06:24:11,979 [MainThread  ] [INFO ]  PROGRESS: at sentence #92740000, processed 1022054007 words and 28131347 word types
2017-10-24 06:24:12,654 [MainThread  ] [INFO ]  PROGRESS: at sentence #92750000, processed 1022163929 words and 28146919 word types
2017-10-24 06:24:13,360 [MainThread  ] [INFO ]  PROGRESS: at sentence #92760000, processed 1022278231 words and 28161479 word types
2017-10-24 06:24:14,089 [MainThread  ] [INFO ]  PROGRESS: at sentence #92770000, processed 1022397595 words and 28176360 word types
2017-10-24 06:24:14,746 [MainThread  ] [INFO ]  PROGRESS: at sentence #92780000, processed 1022500705 words and 28192995 word types
2017-10-24 06:24:15,440 [MainThread  ] [INFO ]  PROGRESS: at sentence #92790000, processed 1022609287 words and 28210672 word types
2017-10-24 06:24:16,114 [MainThread  ] [INFO ]  PROGRESS: at sentence #92800000, processed 1022716969 words and 28220173 word types
2017-10-24 06:24:16,812 [MainThread  ] [INFO ]  PROGRESS: at sentence #92810

2017-10-24 06:24:55,469 [MainThread  ] [INFO ]  PROGRESS: at sentence #93370000, processed 1028982821 words and 29105904 word types
2017-10-24 06:24:56,186 [MainThread  ] [INFO ]  PROGRESS: at sentence #93380000, processed 1029098631 words and 29122753 word types
2017-10-24 06:24:56,896 [MainThread  ] [INFO ]  PROGRESS: at sentence #93390000, processed 1029214450 words and 29136904 word types
2017-10-24 06:24:57,586 [MainThread  ] [INFO ]  PROGRESS: at sentence #93400000, processed 1029326352 words and 29150265 word types
2017-10-24 06:24:58,266 [MainThread  ] [INFO ]  PROGRESS: at sentence #93410000, processed 1029435148 words and 29167195 word types
2017-10-24 06:24:58,965 [MainThread  ] [INFO ]  PROGRESS: at sentence #93420000, processed 1029546186 words and 29187318 word types
2017-10-24 06:24:59,700 [MainThread  ] [INFO ]  PROGRESS: at sentence #93430000, processed 1029666307 words and 29202991 word types
2017-10-24 06:25:00,439 [MainThread  ] [INFO ]  PROGRESS: at sentence #93440

In [33]:
trigram.save('../data/lingvo/trigram')

2017-10-24 06:25:34,038 [MainThread  ] [INFO ]  saving Phrases object under ../data/lingvo/trigram, separately None
2017-10-24 06:26:17,685 [MainThread  ] [INFO ]  saved ../data/lingvo/trigram


In [36]:
trigram = gensim.models.phrases.Phrases.load(join(DATA_FOLDER, '../data/lingvo/trigram'))

2017-10-24 12:24:28,259 [MainThread  ] [INFO ]  loading Phrases object from ../data/../data/lingvo/trigram
2017-10-24 12:24:43,547 [MainThread  ] [INFO ]  loaded ../data/../data/lingvo/trigram


In [39]:
for s in islice(trigram[bigram_ph[iter_sents()]], 1000):
    for w in s:
        if len(w.split('_')) > 2:
            print(w)

суперсплав_никель_направленно
суперсплав_никель_направленно
суперсплав_никель_направленно
кобальт_молибден_вольфрам
суперсплав_никель_направленно
кобальт_молибден_вольфрам
суперсплав_никель_направленно
mo_ta_nb
al_ti_zr
advanced_materials_process
cr_мо_ti
cr_мо_ti
затруднять_делать_невозможный
astm_american_society
test_materials_американский_общество
детектирование_подсинхронный_резонанс
детектирование_подсинхронный_резонанс
среднеквадратичный_rm_демодулировать
rm_rmslev_подсинхронный_резонанс
rm_rmslev_подсинхронный_резонанс
детектирование_подсинхронный_резонанс
детектирование_подсинхронный_резонанс
среднеквадратичный_rm_демодулировать
rm_rmslev_подсинхронный_резонанс
детектирование_подсинхронный_резонанс
явление_подсинхронный_резонанс
явление_подсинхронный_резонанс
детектирование_подсинхронный_резонанс
детектирование_подсинхронный_резонанс
детектирование_подсинхронный_резонанс
явление_подсинхронный_резонанс
детектирование_подсинхронный_резонанс
среднеквадратичный_rm_демодулировать
r

In [40]:
trigram_ph = gensim.models.phrases.Phraser(trigram)
trigram_ph.save('../data/lingvo/trigram_ph')

2017-10-24 09:12:01,557 [MainThread  ] [INFO ]  source_vocab length 29961985
2017-10-24 09:12:08,168 [MainThread  ] [INFO ]  Phraser added 50000 phrasegrams
2017-10-24 09:12:14,629 [MainThread  ] [INFO ]  Phraser added 100000 phrasegrams
2017-10-24 09:12:21,170 [MainThread  ] [INFO ]  Phraser added 150000 phrasegrams
2017-10-24 09:12:27,652 [MainThread  ] [INFO ]  Phraser added 200000 phrasegrams
2017-10-24 09:12:34,117 [MainThread  ] [INFO ]  Phraser added 250000 phrasegrams
2017-10-24 09:12:40,637 [MainThread  ] [INFO ]  Phraser added 300000 phrasegrams
2017-10-24 09:12:47,126 [MainThread  ] [INFO ]  Phraser added 350000 phrasegrams
2017-10-24 09:12:53,535 [MainThread  ] [INFO ]  Phraser added 400000 phrasegrams
2017-10-24 09:12:59,984 [MainThread  ] [INFO ]  Phraser added 450000 phrasegrams
2017-10-24 09:13:06,406 [MainThread  ] [INFO ]  Phraser added 500000 phrasegrams
2017-10-24 09:13:13,090 [MainThread  ] [INFO ]  Phraser added 550000 phrasegrams
2017-10-24 09:13:20,010 [MainThre

In [6]:
trigram_ph = gensim.models.phrases.Phrases.load('../data/lingvo/trigram_ph')

2017-10-24 15:17:25,101 [MainThread  ] [INFO ]  loading Phrases object from ../data/lingvo/trigram_ph
2017-10-24 15:17:27,538 [MainThread  ] [INFO ]  loaded ../data/lingvo/trigram_ph


In [ ]:
model = Word2Vec(Sentences(), size=dim, sg=1, min_count=10, window=10, workers=8)

2017-10-13 12:05:54,498 [MainThread  ] [INFO ]  collecting all words and their counts
2017-10-13 12:05:54,513 [MainThread  ] [INFO ]  PROGRESS: at sentence #0, processed 0 words, keeping 0 word types
2017-10-13 12:05:54,675 [MainThread  ] [INFO ]  PROGRESS: at sentence #10000, processed 108194 words, keeping 11923 word types
2017-10-13 12:05:54,856 [MainThread  ] [INFO ]  PROGRESS: at sentence #20000, processed 215695 words, keeping 18597 word types
2017-10-13 12:05:54,990 [MainThread  ] [INFO ]  PROGRESS: at sentence #30000, processed 333525 words, keeping 25805 word types
2017-10-13 12:05:55,139 [MainThread  ] [INFO ]  PROGRESS: at sentence #40000, processed 456196 words, keeping 32259 word types
2017-10-13 12:05:55,294 [MainThread  ] [INFO ]  PROGRESS: at sentence #50000, processed 580554 words, keeping 37391 word types
2017-10-13 12:05:55,436 [MainThread  ] [INFO ]  PROGRESS: at sentence #60000, processed 695913 words, keeping 41846 word types
2017-10-13 12:05:55,582 [MainThread  ]

2017-10-13 12:06:03,189 [MainThread  ] [INFO ]  PROGRESS: at sentence #630000, processed 6912698 words, keeping 212405 word types
2017-10-13 12:06:03,334 [MainThread  ] [INFO ]  PROGRESS: at sentence #640000, processed 7029422 words, keeping 214492 word types
2017-10-13 12:06:03,479 [MainThread  ] [INFO ]  PROGRESS: at sentence #650000, processed 7143134 words, keeping 216730 word types
2017-10-13 12:06:03,616 [MainThread  ] [INFO ]  PROGRESS: at sentence #660000, processed 7252544 words, keeping 219287 word types
2017-10-13 12:06:03,764 [MainThread  ] [INFO ]  PROGRESS: at sentence #670000, processed 7369004 words, keeping 221799 word types
2017-10-13 12:06:03,894 [MainThread  ] [INFO ]  PROGRESS: at sentence #680000, processed 7474811 words, keeping 223765 word types
2017-10-13 12:06:04,030 [MainThread  ] [INFO ]  PROGRESS: at sentence #690000, processed 7585323 words, keeping 226257 word types
2017-10-13 12:06:04,174 [MainThread  ] [INFO ]  PROGRESS: at sentence #700000, processed 7

2017-10-13 12:06:11,826 [MainThread  ] [INFO ]  PROGRESS: at sentence #1260000, processed 13775627 words, keeping 347112 word types
2017-10-13 12:06:11,961 [MainThread  ] [INFO ]  PROGRESS: at sentence #1270000, processed 13881680 words, keeping 349401 word types
2017-10-13 12:06:12,138 [MainThread  ] [INFO ]  PROGRESS: at sentence #1280000, processed 13998165 words, keeping 352595 word types
2017-10-13 12:06:12,261 [MainThread  ] [INFO ]  PROGRESS: at sentence #1290000, processed 14097940 words, keeping 354205 word types
2017-10-13 12:06:12,403 [MainThread  ] [INFO ]  PROGRESS: at sentence #1300000, processed 14211202 words, keeping 355867 word types
2017-10-13 12:06:12,546 [MainThread  ] [INFO ]  PROGRESS: at sentence #1310000, processed 14321740 words, keeping 357628 word types
2017-10-13 12:06:12,685 [MainThread  ] [INFO ]  PROGRESS: at sentence #1320000, processed 14427613 words, keeping 358908 word types
2017-10-13 12:06:12,833 [MainThread  ] [INFO ]  PROGRESS: at sentence #13300

2017-10-13 12:06:21,036 [MainThread  ] [INFO ]  PROGRESS: at sentence #1890000, processed 20776871 words, keeping 468625 word types
2017-10-13 12:06:21,159 [MainThread  ] [INFO ]  PROGRESS: at sentence #1900000, processed 20888023 words, keeping 470846 word types
2017-10-13 12:06:21,293 [MainThread  ] [INFO ]  PROGRESS: at sentence #1910000, processed 20994697 words, keeping 472655 word types
2017-10-13 12:06:21,465 [MainThread  ] [INFO ]  PROGRESS: at sentence #1920000, processed 21129632 words, keeping 483234 word types
2017-10-13 12:06:21,609 [MainThread  ] [INFO ]  PROGRESS: at sentence #1930000, processed 21241099 words, keeping 484939 word types
2017-10-13 12:06:21,761 [MainThread  ] [INFO ]  PROGRESS: at sentence #1940000, processed 21360694 words, keeping 486726 word types
2017-10-13 12:06:21,915 [MainThread  ] [INFO ]  PROGRESS: at sentence #1950000, processed 21474656 words, keeping 488201 word types
2017-10-13 12:06:22,054 [MainThread  ] [INFO ]  PROGRESS: at sentence #19600

2017-10-13 12:06:35,568 [MainThread  ] [INFO ]  PROGRESS: at sentence #2520000, processed 27727349 words, keeping 580795 word types
2017-10-13 12:06:35,707 [MainThread  ] [INFO ]  PROGRESS: at sentence #2530000, processed 27833182 words, keeping 582434 word types
2017-10-13 12:06:35,848 [MainThread  ] [INFO ]  PROGRESS: at sentence #2540000, processed 27941401 words, keeping 584349 word types
2017-10-13 12:06:35,987 [MainThread  ] [INFO ]  PROGRESS: at sentence #2550000, processed 28051040 words, keeping 586012 word types
2017-10-13 12:06:36,134 [MainThread  ] [INFO ]  PROGRESS: at sentence #2560000, processed 28166192 words, keeping 587900 word types
2017-10-13 12:06:36,292 [MainThread  ] [INFO ]  PROGRESS: at sentence #2570000, processed 28282356 words, keeping 589201 word types
2017-10-13 12:06:36,440 [MainThread  ] [INFO ]  PROGRESS: at sentence #2580000, processed 28395935 words, keeping 590573 word types
2017-10-13 12:06:36,581 [MainThread  ] [INFO ]  PROGRESS: at sentence #25900

...

2017-10-13 17:44:50,706 [MainThread  ] [INFO ]  PROGRESS: at 54.43% examples, 153086 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:44:51,744 [MainThread  ] [INFO ]  PROGRESS: at 54.44% examples, 153086 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:44:52,777 [MainThread  ] [INFO ]  PROGRESS: at 54.44% examples, 153086 words/s, in_qsize 16, out_qsize 0
2017-10-13 17:44:53,803 [MainThread  ] [INFO ]  PROGRESS: at 54.44% examples, 153086 words/s, in_qsize 16, out_qsize 0
2017-10-13 17:44:54,813 [MainThread  ] [INFO ]  PROGRESS: at 54.45% examples, 153086 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:44:55,810 [MainThread  ] [INFO ]  PROGRESS: at 54.45% examples, 153086 words/s, in_qsize 16, out_qsize 0
2017-10-13 17:44:56,826 [MainThread  ] [INFO ]  PROGRESS: at 54.45% examples, 153087 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:44:58,185 [MainThread  ] [INFO ]  PROGRESS: at 54.46% examples, 153083 words/s, in_qsize 16, out_qsize 0
2017-10-13 17:44:59,194 [MainThread  ] [INFO ]  

2017-10-13 17:46:03,322 [MainThread  ] [INFO ]  PROGRESS: at 54.66% examples, 153084 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:46:04,337 [MainThread  ] [INFO ]  PROGRESS: at 54.66% examples, 153084 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:46:05,376 [MainThread  ] [INFO ]  PROGRESS: at 54.67% examples, 153084 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:46:06,398 [MainThread  ] [INFO ]  PROGRESS: at 54.67% examples, 153084 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:46:07,412 [MainThread  ] [INFO ]  PROGRESS: at 54.67% examples, 153084 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:46:08,463 [MainThread  ] [INFO ]  PROGRESS: at 54.68% examples, 153084 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:46:09,471 [MainThread  ] [INFO ]  PROGRESS: at 54.68% examples, 153085 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:46:10,647 [MainThread  ] [INFO ]  PROGRESS: at 54.68% examples, 153084 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:46:11,657 [MainThread  ] [INFO ]  

2017-10-13 17:47:15,934 [MainThread  ] [INFO ]  PROGRESS: at 54.88% examples, 153079 words/s, in_qsize 16, out_qsize 0
2017-10-13 17:47:16,971 [MainThread  ] [INFO ]  PROGRESS: at 54.89% examples, 153080 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:47:18,135 [MainThread  ] [INFO ]  PROGRESS: at 54.89% examples, 153080 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:47:19,199 [MainThread  ] [INFO ]  PROGRESS: at 54.90% examples, 153080 words/s, in_qsize 16, out_qsize 0
2017-10-13 17:47:20,203 [MainThread  ] [INFO ]  PROGRESS: at 54.90% examples, 153080 words/s, in_qsize 16, out_qsize 0
2017-10-13 17:47:21,303 [MainThread  ] [INFO ]  PROGRESS: at 54.90% examples, 153080 words/s, in_qsize 16, out_qsize 0
2017-10-13 17:47:22,319 [MainThread  ] [INFO ]  PROGRESS: at 54.91% examples, 153081 words/s, in_qsize 16, out_qsize 0
2017-10-13 17:47:23,362 [MainThread  ] [INFO ]  PROGRESS: at 54.91% examples, 153082 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:47:24,407 [MainThread  ] [INFO ]  

2017-10-13 17:48:30,062 [MainThread  ] [INFO ]  PROGRESS: at 55.12% examples, 153080 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:48:31,133 [MainThread  ] [INFO ]  PROGRESS: at 55.12% examples, 153081 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:48:32,139 [MainThread  ] [INFO ]  PROGRESS: at 55.12% examples, 153082 words/s, in_qsize 16, out_qsize 0
2017-10-13 17:48:33,141 [MainThread  ] [INFO ]  PROGRESS: at 55.13% examples, 153082 words/s, in_qsize 16, out_qsize 0
2017-10-13 17:48:34,168 [MainThread  ] [INFO ]  PROGRESS: at 55.13% examples, 153081 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:48:35,315 [MainThread  ] [INFO ]  PROGRESS: at 55.13% examples, 153081 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:48:36,310 [MainThread  ] [INFO ]  PROGRESS: at 55.14% examples, 153081 words/s, in_qsize 16, out_qsize 0
2017-10-13 17:48:37,471 [MainThread  ] [INFO ]  PROGRESS: at 55.14% examples, 153081 words/s, in_qsize 16, out_qsize 0
2017-10-13 17:48:38,524 [MainThread  ] [INFO ]  

2017-10-13 17:49:43,067 [MainThread  ] [INFO ]  PROGRESS: at 55.34% examples, 153079 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:49:44,199 [MainThread  ] [INFO ]  PROGRESS: at 55.35% examples, 153079 words/s, in_qsize 16, out_qsize 0
2017-10-13 17:49:45,225 [MainThread  ] [INFO ]  PROGRESS: at 55.35% examples, 153080 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:49:46,251 [MainThread  ] [INFO ]  PROGRESS: at 55.35% examples, 153080 words/s, in_qsize 16, out_qsize 0
2017-10-13 17:49:47,305 [MainThread  ] [INFO ]  PROGRESS: at 55.36% examples, 153081 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:49:48,308 [MainThread  ] [INFO ]  PROGRESS: at 55.36% examples, 153080 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:49:49,322 [MainThread  ] [INFO ]  PROGRESS: at 55.36% examples, 153080 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:49:50,381 [MainThread  ] [INFO ]  PROGRESS: at 55.37% examples, 153081 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:49:51,420 [MainThread  ] [INFO ]  

In [ ]:
model.save('../data/lingvo/w2v_300_sg_10_w10')

In [ ]:
model = Word2Vec(trigram_ph[Sentences()], size=dim, sg=1, min_count=5, window=10, workers=cpu_count)

2017-10-24 15:17:35,534 [MainThread  ] [INFO ]  collecting all words and their counts
2017-10-24 15:17:35,536 [MainThread  ] [INFO ]  PROGRESS: at sentence #0, processed 0 words, keeping 0 word types
2017-10-24 15:17:36,108 [MainThread  ] [INFO ]  PROGRESS: at sentence #10000, processed 115572 words, keeping 13487 word types
2017-10-24 15:17:36,659 [MainThread  ] [INFO ]  PROGRESS: at sentence #20000, processed 229269 words, keeping 22139 word types
2017-10-24 15:17:37,177 [MainThread  ] [INFO ]  PROGRESS: at sentence #30000, processed 333107 words, keeping 30202 word types
2017-10-24 15:17:37,700 [MainThread  ] [INFO ]  PROGRESS: at sentence #40000, processed 439004 words, keeping 39155 word types
2017-10-24 15:17:38,195 [MainThread  ] [INFO ]  PROGRESS: at sentence #50000, processed 537897 words, keeping 44921 word types
2017-10-24 15:17:38,757 [MainThread  ] [INFO ]  PROGRESS: at sentence #60000, processed 652063 words, keeping 52036 word types
2017-10-24 15:17:39,333 [MainThread  ]

2017-10-24 15:18:09,845 [MainThread  ] [INFO ]  PROGRESS: at sentence #630000, processed 6760453 words, keeping 305972 word types
2017-10-24 15:18:10,372 [MainThread  ] [INFO ]  PROGRESS: at sentence #640000, processed 6865165 words, keeping 311197 word types
2017-10-24 15:18:10,918 [MainThread  ] [INFO ]  PROGRESS: at sentence #650000, processed 6973193 words, keeping 314891 word types
2017-10-24 15:18:11,498 [MainThread  ] [INFO ]  PROGRESS: at sentence #660000, processed 7077497 words, keeping 318493 word types
2017-10-24 15:18:12,057 [MainThread  ] [INFO ]  PROGRESS: at sentence #670000, processed 7190685 words, keeping 321330 word types
2017-10-24 15:18:12,632 [MainThread  ] [INFO ]  PROGRESS: at sentence #680000, processed 7303895 words, keeping 324566 word types
2017-10-24 15:18:13,207 [MainThread  ] [INFO ]  PROGRESS: at sentence #690000, processed 7420663 words, keeping 327598 word types
2017-10-24 15:18:13,748 [MainThread  ] [INFO ]  PROGRESS: at sentence #700000, processed 7

2017-10-24 15:18:43,629 [MainThread  ] [INFO ]  PROGRESS: at sentence #1260000, processed 13478755 words, keeping 522120 word types
2017-10-24 15:18:44,192 [MainThread  ] [INFO ]  PROGRESS: at sentence #1270000, processed 13590289 words, keeping 525048 word types
2017-10-24 15:18:44,752 [MainThread  ] [INFO ]  PROGRESS: at sentence #1280000, processed 13700599 words, keeping 528119 word types
2017-10-24 15:18:45,311 [MainThread  ] [INFO ]  PROGRESS: at sentence #1290000, processed 13812464 words, keeping 530692 word types
2017-10-24 15:18:45,865 [MainThread  ] [INFO ]  PROGRESS: at sentence #1300000, processed 13921581 words, keeping 533401 word types
2017-10-24 15:18:46,394 [MainThread  ] [INFO ]  PROGRESS: at sentence #1310000, processed 14026751 words, keeping 537016 word types
2017-10-24 15:18:46,919 [MainThread  ] [INFO ]  PROGRESS: at sentence #1320000, processed 14129897 words, keeping 540047 word types
2017-10-24 15:18:47,484 [MainThread  ] [INFO ]  PROGRESS: at sentence #13300

2017-10-24 15:19:17,451 [MainThread  ] [INFO ]  PROGRESS: at sentence #1890000, processed 20202404 words, keeping 712147 word types
2017-10-24 15:19:17,944 [MainThread  ] [INFO ]  PROGRESS: at sentence #1900000, processed 20293530 words, keeping 714562 word types
2017-10-24 15:19:18,471 [MainThread  ] [INFO ]  PROGRESS: at sentence #1910000, processed 20397232 words, keeping 717728 word types
2017-10-24 15:19:19,013 [MainThread  ] [INFO ]  PROGRESS: at sentence #1920000, processed 20506342 words, keeping 719760 word types
2017-10-24 15:19:19,598 [MainThread  ] [INFO ]  PROGRESS: at sentence #1930000, processed 20625361 words, keeping 722219 word types
2017-10-24 15:19:20,115 [MainThread  ] [INFO ]  PROGRESS: at sentence #1940000, processed 20725421 words, keeping 724230 word types
2017-10-24 15:19:20,633 [MainThread  ] [INFO ]  PROGRESS: at sentence #1950000, processed 20829651 words, keeping 726618 word types
2017-10-24 15:19:21,160 [MainThread  ] [INFO ]  PROGRESS: at sentence #19600

2017-10-24 15:19:51,413 [MainThread  ] [INFO ]  PROGRESS: at sentence #2520000, processed 26904056 words, keeping 878208 word types
2017-10-24 15:19:51,963 [MainThread  ] [INFO ]  PROGRESS: at sentence #2530000, processed 27011507 words, keeping 880409 word types
2017-10-24 15:19:52,529 [MainThread  ] [INFO ]  PROGRESS: at sentence #2540000, processed 27122317 words, keeping 882213 word types
2017-10-24 15:19:53,098 [MainThread  ] [INFO ]  PROGRESS: at sentence #2550000, processed 27235172 words, keeping 885358 word types
2017-10-24 15:19:53,639 [MainThread  ] [INFO ]  PROGRESS: at sentence #2560000, processed 27341670 words, keeping 887528 word types
2017-10-24 15:19:54,192 [MainThread  ] [INFO ]  PROGRESS: at sentence #2570000, processed 27453593 words, keeping 889609 word types
2017-10-24 15:19:54,726 [MainThread  ] [INFO ]  PROGRESS: at sentence #2580000, processed 27559210 words, keeping 891644 word types
2017-10-24 15:19:55,254 [MainThread  ] [INFO ]  PROGRESS: at sentence #25900

2017-10-24 15:20:25,781 [MainThread  ] [INFO ]  PROGRESS: at sentence #3140000, processed 33591986 words, keeping 1030911 word types
2017-10-24 15:20:26,365 [MainThread  ] [INFO ]  PROGRESS: at sentence #3150000, processed 33699589 words, keeping 1033007 word types
2017-10-24 15:20:26,940 [MainThread  ] [INFO ]  PROGRESS: at sentence #3160000, processed 33808391 words, keeping 1034952 word types
2017-10-24 15:20:27,502 [MainThread  ] [INFO ]  PROGRESS: at sentence #3170000, processed 33914675 words, keeping 1036595 word types
2017-10-24 15:20:28,057 [MainThread  ] [INFO ]  PROGRESS: at sentence #3180000, processed 34021783 words, keeping 1038654 word types
2017-10-24 15:20:28,625 [MainThread  ] [INFO ]  PROGRESS: at sentence #3190000, processed 34132035 words, keeping 1041497 word types
2017-10-24 15:20:29,201 [MainThread  ] [INFO ]  PROGRESS: at sentence #3200000, processed 34242805 words, keeping 1043661 word types
2017-10-24 15:20:29,770 [MainThread  ] [INFO ]  PROGRESS: at sentence

In [ ]:
model.save('../data/lingvo/w2v_300_sg_5_w10_trigram')

In [34]:
!ls ../data/lingvo/w2v_300_sg_5_w10_trigram

ls: cannot access '../data/lingvo/w2v_300_sg_5_w10_trigram': No such file or directory


In [25]:
!ls -sh ../data/lingvo/w2v_300_sg_5_w10_trigram

241M ../data/lingvo/w2v_300_sg_5_w10_trigram


# Doc2Vec

In [ ]:
model = Doc2Vec(Documents(), size=300, window=8, min_count=5, dm=1, workers=cpu_count-1)

2017-10-14 04:11:08,850 [MainThread  ] [INFO ]  collecting all words and their counts
2017-10-14 04:11:08,854 [MainThread  ] [INFO ]  PROGRESS: at example #0, processed 0 words (0/s), 0 word types, 0 tags
2017-10-14 04:11:19,029 [MainThread  ] [INFO ]  PROGRESS: at example #10000, processed 8123140 words (798439/s), 236646 word types, 10000 tags
2017-10-14 04:11:29,318 [MainThread  ] [INFO ]  PROGRESS: at example #20000, processed 16424932 words (807042/s), 394754 word types, 20000 tags
2017-10-14 04:11:39,616 [MainThread  ] [INFO ]  PROGRESS: at example #30000, processed 24640670 words (797992/s), 534330 word types, 30000 tags
2017-10-14 04:11:49,727 [MainThread  ] [INFO ]  PROGRESS: at example #40000, processed 32746968 words (801854/s), 653669 word types, 40000 tags
2017-10-14 04:11:59,823 [MainThread  ] [INFO ]  PROGRESS: at example #50000, processed 40811158 words (798911/s), 763362 word types, 50000 tags
2017-10-14 04:12:09,537 [MainThread  ] [INFO ]  PROGRESS: at example #60000,

2017-10-14 04:28:33,357 [MainThread  ] [INFO ]  PROGRESS: at example #1000000, processed 822139110 words (796578/s), 6568441 word types, 1000000 tags
2017-10-14 04:28:43,898 [MainThread  ] [INFO ]  PROGRESS: at example #1010000, processed 830455121 words (788996/s), 6617694 word types, 1010000 tags
2017-10-14 04:28:54,400 [MainThread  ] [INFO ]  PROGRESS: at example #1020000, processed 838811802 words (795839/s), 6666938 word types, 1020000 tags
2017-10-14 04:29:04,442 [MainThread  ] [INFO ]  PROGRESS: at example #1030000, processed 846868001 words (802325/s), 6714353 word types, 1030000 tags
2017-10-14 04:29:14,646 [MainThread  ] [INFO ]  PROGRESS: at example #1040000, processed 855081541 words (805088/s), 6761334 word types, 1040000 tags
2017-10-14 04:29:24,810 [MainThread  ] [INFO ]  PROGRESS: at example #1050000, processed 863168364 words (795767/s), 6803477 word types, 1050000 tags
2017-10-14 04:29:35,227 [MainThread  ] [INFO ]  PROGRESS: at example #1060000, processed 871346969 w

2017-10-14 04:34:42,886 [MainThread  ] [INFO ]  PROGRESS: at 0.24% examples, 338659 words/s, in_qsize 0, out_qsize 0
2017-10-14 04:34:43,976 [MainThread  ] [INFO ]  PROGRESS: at 0.25% examples, 338365 words/s, in_qsize 0, out_qsize 1
2017-10-14 04:34:44,993 [MainThread  ] [INFO ]  PROGRESS: at 0.25% examples, 338995 words/s, in_qsize 0, out_qsize 0
2017-10-14 04:34:46,021 [MainThread  ] [INFO ]  PROGRESS: at 0.26% examples, 339281 words/s, in_qsize 0, out_qsize 0
2017-10-14 04:34:47,024 [MainThread  ] [INFO ]  PROGRESS: at 0.27% examples, 339326 words/s, in_qsize 0, out_qsize 0
2017-10-14 04:34:48,032 [MainThread  ] [INFO ]  PROGRESS: at 0.27% examples, 339289 words/s, in_qsize 0, out_qsize 0
2017-10-14 04:34:49,072 [MainThread  ] [INFO ]  PROGRESS: at 0.28% examples, 339036 words/s, in_qsize 0, out_qsize 1
2017-10-14 04:34:50,073 [MainThread  ] [INFO ]  PROGRESS: at 0.29% examples, 339677 words/s, in_qsize 0, out_qsize 0
2017-10-14 04:34:51,081 [MainThread  ] [INFO ]  PROGRESS: at 0.3

2017-10-14 04:35:55,354 [MainThread  ] [INFO ]  PROGRESS: at 0.76% examples, 341927 words/s, in_qsize 0, out_qsize 0
2017-10-14 04:35:56,357 [MainThread  ] [INFO ]  PROGRESS: at 0.77% examples, 342049 words/s, in_qsize 0, out_qsize 0
2017-10-14 04:35:57,365 [MainThread  ] [INFO ]  PROGRESS: at 0.78% examples, 341993 words/s, in_qsize 0, out_qsize 0
2017-10-14 04:35:58,374 [MainThread  ] [INFO ]  PROGRESS: at 0.79% examples, 342004 words/s, in_qsize 0, out_qsize 0
2017-10-14 04:35:59,433 [MainThread  ] [INFO ]  PROGRESS: at 0.79% examples, 341791 words/s, in_qsize 0, out_qsize 0
2017-10-14 04:36:00,437 [MainThread  ] [INFO ]  PROGRESS: at 0.80% examples, 341914 words/s, in_qsize 0, out_qsize 0
2017-10-14 04:36:01,445 [MainThread  ] [INFO ]  PROGRESS: at 0.81% examples, 341858 words/s, in_qsize 0, out_qsize 0
2017-10-14 04:36:02,449 [MainThread  ] [INFO ]  PROGRESS: at 0.81% examples, 342030 words/s, in_qsize 0, out_qsize 0
2017-10-14 04:36:03,454 [MainThread  ] [INFO ]  PROGRESS: at 0.8

2017-10-14 04:37:07,727 [MainThread  ] [INFO ]  PROGRESS: at 1.30% examples, 343877 words/s, in_qsize 0, out_qsize 0
2017-10-14 04:37:08,739 [MainThread  ] [INFO ]  PROGRESS: at 1.30% examples, 343882 words/s, in_qsize 0, out_qsize 0
2017-10-14 04:37:09,752 [MainThread  ] [INFO ]  PROGRESS: at 1.31% examples, 344014 words/s, in_qsize 0, out_qsize 0
2017-10-14 04:37:10,778 [MainThread  ] [INFO ]  PROGRESS: at 1.32% examples, 344198 words/s, in_qsize 0, out_qsize 0
2017-10-14 04:37:11,790 [MainThread  ] [INFO ]  PROGRESS: at 1.33% examples, 344375 words/s, in_qsize 0, out_qsize 1
2017-10-14 04:37:12,794 [MainThread  ] [INFO ]  PROGRESS: at 1.33% examples, 344473 words/s, in_qsize 0, out_qsize 0
2017-10-14 04:37:13,877 [MainThread  ] [INFO ]  PROGRESS: at 1.34% examples, 344486 words/s, in_qsize 0, out_qsize 1
2017-10-14 04:37:14,912 [MainThread  ] [INFO ]  PROGRESS: at 1.35% examples, 344550 words/s, in_qsize 0, out_qsize 0
2017-10-14 04:37:15,959 [MainThread  ] [INFO ]  PROGRESS: at 1.3

...

2017-10-14 05:40:28,222 [MainThread  ] [INFO ]  PROGRESS: at 29.13% examples, 349797 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:40:29,229 [MainThread  ] [INFO ]  PROGRESS: at 29.14% examples, 349798 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:40:30,231 [MainThread  ] [INFO ]  PROGRESS: at 29.14% examples, 349797 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:40:31,258 [MainThread  ] [INFO ]  PROGRESS: at 29.15% examples, 349793 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:40:32,282 [MainThread  ] [INFO ]  PROGRESS: at 29.16% examples, 349789 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:40:33,336 [MainThread  ] [INFO ]  PROGRESS: at 29.17% examples, 349787 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:40:34,349 [MainThread  ] [INFO ]  PROGRESS: at 29.17% examples, 349791 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:40:35,380 [MainThread  ] [INFO ]  PROGRESS: at 29.18% examples, 349793 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:40:36,399 [MainThread  ] [INFO ]  PROGRESS

2017-10-14 05:41:39,484 [MainThread  ] [INFO ]  PROGRESS: at 29.65% examples, 349849 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:41:40,502 [MainThread  ] [INFO ]  PROGRESS: at 29.66% examples, 349851 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:41:41,542 [MainThread  ] [INFO ]  PROGRESS: at 29.66% examples, 349853 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:41:42,558 [MainThread  ] [INFO ]  PROGRESS: at 29.67% examples, 349854 words/s, in_qsize 0, out_qsize 1
2017-10-14 05:41:43,586 [MainThread  ] [INFO ]  PROGRESS: at 29.68% examples, 349857 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:41:44,601 [MainThread  ] [INFO ]  PROGRESS: at 29.69% examples, 349856 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:41:45,618 [MainThread  ] [INFO ]  PROGRESS: at 29.69% examples, 349857 words/s, in_qsize 1, out_qsize 0
2017-10-14 05:41:46,649 [MainThread  ] [INFO ]  PROGRESS: at 29.70% examples, 349855 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:41:47,699 [MainThread  ] [INFO ]  PROGRESS

2017-10-14 05:42:50,656 [MainThread  ] [INFO ]  PROGRESS: at 30.18% examples, 349910 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:42:51,668 [MainThread  ] [INFO ]  PROGRESS: at 30.18% examples, 349909 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:42:52,671 [MainThread  ] [INFO ]  PROGRESS: at 30.19% examples, 349911 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:42:53,689 [MainThread  ] [INFO ]  PROGRESS: at 30.20% examples, 349908 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:42:54,704 [MainThread  ] [INFO ]  PROGRESS: at 30.20% examples, 349905 words/s, in_qsize 0, out_qsize 1
2017-10-14 05:42:55,737 [MainThread  ] [INFO ]  PROGRESS: at 30.21% examples, 349910 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:42:56,738 [MainThread  ] [INFO ]  PROGRESS: at 30.22% examples, 349908 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:42:57,788 [MainThread  ] [INFO ]  PROGRESS: at 30.23% examples, 349907 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:42:58,795 [MainThread  ] [INFO ]  PROGRESS

2017-10-14 05:44:02,099 [MainThread  ] [INFO ]  PROGRESS: at 30.70% examples, 349915 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:44:03,113 [MainThread  ] [INFO ]  PROGRESS: at 30.71% examples, 349916 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:44:04,142 [MainThread  ] [INFO ]  PROGRESS: at 30.71% examples, 349916 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:44:05,154 [MainThread  ] [INFO ]  PROGRESS: at 30.72% examples, 349921 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:44:06,213 [MainThread  ] [INFO ]  PROGRESS: at 30.73% examples, 349916 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:44:07,225 [MainThread  ] [INFO ]  PROGRESS: at 30.74% examples, 349924 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:44:08,235 [MainThread  ] [INFO ]  PROGRESS: at 30.74% examples, 349924 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:44:09,241 [MainThread  ] [INFO ]  PROGRESS: at 30.75% examples, 349924 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:44:10,242 [MainThread  ] [INFO ]  PROGRESS

2017-10-14 05:45:13,516 [MainThread  ] [INFO ]  PROGRESS: at 31.22% examples, 349920 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:45:14,538 [MainThread  ] [INFO ]  PROGRESS: at 31.22% examples, 349918 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:45:15,565 [MainThread  ] [INFO ]  PROGRESS: at 31.23% examples, 349922 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:45:16,576 [MainThread  ] [INFO ]  PROGRESS: at 31.24% examples, 349921 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:45:17,596 [MainThread  ] [INFO ]  PROGRESS: at 31.25% examples, 349923 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:45:18,628 [MainThread  ] [INFO ]  PROGRESS: at 31.25% examples, 349924 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:45:19,637 [MainThread  ] [INFO ]  PROGRESS: at 31.26% examples, 349924 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:45:20,646 [MainThread  ] [INFO ]  PROGRESS: at 31.27% examples, 349923 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:45:21,650 [MainThread  ] [INFO ]  PROGRESS

In [ ]:
model.save('../data/lingvo/d2v_s300_w8_mc5_dm1_iter5')

# Save for Misha

In [5]:
trigram_ph = gensim.models.phrases.Phraser.load('../data/lingvo/trigram_ph')

2017-10-24 09:33:56,826 [MainThread  ] [INFO ]  loading Phraser object from ../data/lingvo/trigram_ph
2017-10-24 09:33:58,577 [MainThread  ] [INFO ]  loaded ../data/lingvo/trigram_ph


In [32]:
c = 0
l = []
for k,v in tqdm_notebook(trigram_ph.phrasegrams.items()):
    if v[0] > 5 and v[1] > 10:
        the_string = '_'.join(k)
        if re.search('[а-яА-Яa-zA-Z]', k[0]) and re.search('[а-яА-Яa-zA-Z]', k[1]):
            c+=1
            l.append([the_string, v[0], v[1]])
#         print('%s_%s %s' % (k[0], k[1], v))
        
df = pd.DataFrame(l)

In [17]:
for i in v:
    print(i)

12
607.786920638


In [ ]:
# df.sort_values(by=1, ascending=False)

In [33]:
len(df[0].unique())

2484751

In [34]:
with GzipFile('../data/collocations_bigram_all.txt.gz', 'w') as f:
    for tag in sorted(df[0].unique()):
        f.write(tag + '\n')

In [2]:
import xml.etree.ElementTree as ET

tree = ET.parse('../data/TestDocumentsResult.xml')
root = tree.getroot()

In [30]:
gold = {}
for child in root:
    sims = []
    for similars in child:
        for sim in similars:
            sims.append(sim.attrib['docId'])
    gold[child.attrib['docId']] = sims